In [1]:
import numpy as np
from scipy.misc import face
from scipy.ndimage import zoom
from scipy.special import logsumexp
import torch
import matplotlib.pyplot as plt
import pickle
import scipy.io
import cv2
import os
import pandas as pd
from scipy.stats import pearsonr, spearmanr

In [ ]:
def load_images_from_folder(folder):
    images = []
    img_name = []
    for filename in os.listdir(folder):
        img = cv2.imread(os.path.join(folder,filename))
        if img is not None:
            images.append(img)
            img_name.append(filename)
    return images, img_name

In [ ]:
imgs, img_name = load_images_from_folder('stimuli')

In [ ]:
img_name

In [ ]:
len(scipy.io.loadmat(fn)['Results']['Disp'])

In [ ]:
fn = '/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/results/S04/FA_Block1.mat'

In [ ]:
len(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][63][0])

In [ ]:
fn = '/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/results/S04/FA_Block1.mat'

for i in range(64):
    gavx, gavy, sttime, entime = [], [], [], []
    
    for j in range(len(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0])):
        gavx.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][18][0][0])
        gavy.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][19][0][0])
        sttime.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][4][0][0])
        entime.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][5][0][0])

    fixendtimes       = scipy.io.loadmat(fn)['Results']['FixEndTimes'][0][0][0][i][0]
    stim_image_name   = scipy.io.loadmat(fn)['Results']['ImPath'][0][0][0][i][0].split('\\')[-1]
    stim_folder_name  = scipy.io.loadmat(fn)['Results']['ImPath'][0][0][0][i][0].split('\\')[-2]

    break

gavx   = np.array(gavx)
gavy   = np.array(gavy)
sttime = np.array(sttime)
entime = np.array(entime)

res_width   = scipy.io.loadmat(fn)['Results']['Disp'][0][0][0][0][2][0][0][0][0][0]
res_height  = scipy.io.loadmat(fn)['Results']['Disp'][0][0][0][0][2][0][0][1][0][0]
ImWidth     = scipy.io.loadmat(fn)['Results']['ImWidth'][0][0][0][0]
ImHeight    = scipy.io.loadmat(fn)['Results']['ImHeight'][0][0][0][0]

FixX = np.round(gavx) - (res_width/2) + (ImWidth/2)
FixY = np.round(gavy) - (res_height/2) + (ImHeight/2)
FixDur = entime - sttime
FixOnset = fixendtimes - FixDur + FixDur*.999

exclude_ind = np.unique([np.where(FixDur < 100)[0][0], np.where(FixOnset < 0)[0][0]])
FixX = np.delete(FixX, exclude_ind)
FixY = np.delete(FixY, exclude_ind)
FixDur = np.delete(FixDur, exclude_ind)
FixOnset = np.delete(FixOnset, exclude_ind)




In [ ]:
image = cv2.imread('/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/stimuli/' + stim_folder_name + '/' + stim_image_name)
image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
image = cv2.resize(image, (ImWidth, ImHeight))
plt.imshow(image)




In [ ]:
image.shape

In [ ]:
scipy.io.loadmat(fn)['Results']['ImPath'][0][0][0][i][0].split('\\')[-2]

In [ ]:

#fixation_history_x = fix_X[i]/3
#print(fixation_history_x)
#fixation_history_y = fix_Y[i]/3
#radius_history = radius[i]/5

#print(fixation_history_x, fixation_history_y, radius_history)

# Create a 2D matrix filled with zeros of size (600, 800)
matrix_size = (1200, 1200)
matrix = np.zeros(matrix_size, dtype=int)

# Call the function to add circles to the matrix
result_matrix = add_circles(matrix, FixY, FixX, FixDur/5)


In [ ]:
plt.imshow(result_matrix)

In [ ]:
FixX(iFix) = round(FixData(iFix).gavx - Results.Disp.Resolution.width./2 + Results.ImWidth/2); 
FixY(iFix) = round(FixData(iFix).gavy - Results.Disp.Resolution.height./2 + Results.ImHeight/2);
FixDur(iFix) = FixData(iFix).entime - FixData(iFix).sttime;
FixOnset(iFix) = Results.FixEndTimes{iIm}(iFix) - FixDur(iFix);
% Bug fix to correct error in fixation onsets
FixOnset(iFix) = FixOnset(iFix) + FixDur(iFix)*.999;

In [ ]:
def load_fix_from_folder(folder):
    fix_X = []
    fix_Y = []
    radius = []
    img_name = []
    for filename in os.listdir(folder):
        fix_X.append(scipy.io.loadmat(os.path.join(folder,filename))['currImData'][:,4])
        fix_Y.append(scipy.io.loadmat(os.path.join(folder,filename))['currImData'][:,5])
        radius.append(scipy.io.loadmat(os.path.join(folder,filename))['currImData'][:,6])
        img_name.append(str(scipy.io.loadmat(os.path.join(folder,filename))['currImName'][0][0]) + '.jpg')
        #print(filename)
        #print(img_name)
    return fix_X, fix_Y, radius, img_name

In [ ]:
import os

def create_folder(folder_path):
    try:
        os.mkdir(folder_path)
        print(f"Folder '{folder_path}' created successfully.")
    except FileExistsError:
        print(f"Folder '{folder_path}' already exists.")
    except Exception as e:
        print(f"An error occurred: {e}")

In [4]:
import os

def folder_exists(folder_path):
    return os.path.exists(folder_path) and os.path.isdir(folder_path)


In [ ]:
def add_circles(matrix, x_list, y_list, r_list):
    for x, y, r in zip(x_list, y_list, r_list):
        x, y, r = int(x), int(y), int(r)
        for i in range(max(0, y - r), min(matrix.shape[0], y + r + 1)):
            for j in range(max(0, x - r), min(matrix.shape[1], x + r + 1)):
                if (i - y) ** 2 + (j - x) ** 2 <= r ** 2:
                    matrix[i][j] += 1
    return matrix

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from scipy.misc import face
from scipy.ndimage import zoom
from scipy.special import logsumexp
import torch

import deepgaze_pytorch

DEVICE = 'cuda'

# you can use DeepGazeI or DeepGazeIIE
model = deepgaze_pytorch.DeepGazeIII(pretrained=True).to(DEVICE)

#image = face()

n_f = '/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens_(1)/results/S'

for q in range(30, 41):
    
    x = []
    
    # Replace 'path/to/your/folder' with the folder path you want to check
    folder_path = n_f + str(q)
    
    if folder_exists(folder_path):
    
        #fix_X, fix_Y, radius, img_name = load_fix_from_folder('S_fix/S'+ str(q) +'_fix')

        # Replace 'path/to/your/folder' with the desired folder path
        folder_path = '/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/DG3_HG_heatmaps_c/S'+ str(q) +'_fix_c'
        create_folder(folder_path)

        for file in sorted(os.listdir(n_f + str(q))):
            if 'Block' in file:
                print(file)        

                fn = n_f + str(q) + '/' + file

                for i in range(64):
                    gavx, gavy, sttime, entime = [], [], [], []

                    for j in range(len(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0])):
                        gavx.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][18][0][0])
                        gavy.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][19][0][0])
                        sttime.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][4][0][0])
                        entime.append(scipy.io.loadmat(fn)['Results']['FixData'][0][0][0][i][0][j][5][0][0])

                    fixendtimes       = scipy.io.loadmat(fn)['Results']['FixEndTimes'][0][0][0][i][0]
                    stim_image_name   = scipy.io.loadmat(fn)['Results']['ImPath'][0][0][0][i][0].split('\\')[-1]
                    stim_folder_name  = scipy.io.loadmat(fn)['Results']['ImPath'][0][0][0][i][0].split('\\')[-2]

                    #break

                    gavx   = np.array(gavx)
                    gavy   = np.array(gavy)
                    sttime = np.array(sttime)
                    entime = np.array(entime)

                    res_width   = scipy.io.loadmat(fn)['Results']['Disp'][0][0][0][0][2][0][0][0][0][0]
                    res_height  = scipy.io.loadmat(fn)['Results']['Disp'][0][0][0][0][2][0][0][1][0][0]
                    ImWidth     = scipy.io.loadmat(fn)['Results']['ImWidth'][0][0][0][0]
                    ImHeight    = scipy.io.loadmat(fn)['Results']['ImHeight'][0][0][0][0]

                    FixX = np.round(gavx) - (res_width/2) + (ImWidth/2)
                    FixY = np.round(gavy) - (res_height/2) + (ImHeight/2)
                    FixDur = entime - sttime
                    FixOnset = fixendtimes - FixDur + FixDur
                    
                    #print(FixDur)
                    #print(FixOnset)
                    dur_indices = np.where(FixDur < 100)[0]
                    onset_indices = np.where(FixOnset < 0)[0]

                    exclude_ind = np.unique(np.concatenate([dur_indices, onset_indices]))
        
                    print(exclude_ind)
                    FixX = np.delete(FixX, exclude_ind)
                    FixY = np.delete(FixY, exclude_ind)
                    FixDur = np.delete(FixDur, exclude_ind)
                    FixOnset = np.delete(FixOnset, exclude_ind)        
            
                    image = cv2.imread('/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/stimuli/' + stim_folder_name + '/' + stim_image_name)
                    create_folder(os.path.join(folder_path, stim_folder_name))
                    
                    #image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
                    image = cv2.resize(image, (ImWidth, ImHeight))             
                
                    if image is not None and len(FixX) > 3 and len(FixY > 3):

                        # location of previous scanpath fixations in x and y (pixel coordinates), starting with the initial fixation on the image.
                        #fixation_history_x = np.array([1024//2, 300, 500, 200, 200, 700])
                        #fixation_history_y = np.array([768//2, 300, 100, 300, 100, 500])

                        #print(img_name[i])

                        fixation_history_x = FixX
                        #print(fixation_history_x)
                        fixation_history_y = FixY
                        #radius_history = radius[i]/5

                        #print(fixation_history_x, fixation_history_y, radius_history)

                        # Create a 2D matrix filled with zeros of size (600, 800)
                        matrix_size = (ImWidth, ImHeight)
                        matrix = np.zeros(matrix_size, dtype=int)

                        # Call the function to add circles to the matrix
                        result_matrix = add_circles(matrix, FixX, FixY, FixDur/5)

                        #plt.imshow(result_matrix)
                        #plt.plot(fixation_history_x, fixation_history_y, 'o-', color='red')
                        #plt.axis('on')
                        #plt.colorbar(fraction=0.046, pad=0.04)  # Adjust fraction and pad values as needed
                        #plt.tight_layout()

                        # load precomputed centerbias log density (from MIT1003) over a 1024x1024 image
                        # you can download the centerbias from https://github.com/matthias-k/DeepGaze/releases/download/v1.0.0/centerbias_mit1003.npy
                        # alternatively, you can use a uniform centerbias via `centerbias_template = np.zeros((1024, 1024))`.
                        centerbias_template = np.load('centerbias_mit1003.npy')

                        # rescale to match image size
                        centerbias = zoom(centerbias_template, (image.shape[0]/centerbias_template.shape[0], image.shape[1]/centerbias_template.shape[1]), order=0, mode='nearest')
                        # renormalize log density
                        centerbias -= logsumexp(centerbias)

                        image_tensor = torch.tensor([image.transpose(2, 0, 1)]).to(DEVICE)
                        centerbias_tensor = torch.tensor([centerbias]).to(DEVICE)
                        x_hist_tensor = torch.tensor([fixation_history_x[model.included_fixations]]).to(DEVICE)
                        y_hist_tensor = torch.tensor([fixation_history_y[model.included_fixations]]).to(DEVICE)

                        log_density_prediction = model(image_tensor, centerbias_tensor, x_hist_tensor, y_hist_tensor)

                        # Scale factor
                        #scale_factor = 3

                        # Calculate the new width and height
                        #new_width = image.shape[1] * scale_factor
                        #new_height = image.shape[0] * scale_factor

                        # Resize the image using cv2.resize()
                        #image = cv2.resize(image, (new_width, new_height))

                        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

                        x.append((log_density_prediction.detach().cpu().numpy()[0, 0], str(stim_folder_name), str(stim_image_name.split('.')[0]),
                                  'S' + str(q), result_matrix))

                        f, axs = plt.subplots(nrows=1, ncols=3, figsize=(16, 9))
                        axs[0].imshow(image)
                        axs[0].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
                        axs[0].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
                        axs[0].set_axis_off()
                        axs[1].matshow(log_density_prediction.detach().cpu().numpy()[0, 0])  # first image in batch, first (and only) channel
                        axs[1].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
                        axs[1].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
                        axs[1].set_axis_off()
                        axs[2].matshow(result_matrix)
                        axs[2].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
                        axs[2].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
                        axs[2].set_axis_off()
                        plt.tight_layout()
                        plt.savefig(os.path.join(folder_path, stim_folder_name, stim_image_name.split('.')[0] + '.png'))
                        #plt.show()
                        plt.close()
                    #break

                # Open a file in binary write mode
                with open(folder_path + '/' + 'S' + str(q) + '.pkl', 'wb') as file:
                    pickle.dump(x, file)

                #break
            #break

In [ ]:
np.shape(x)

In [ ]:
32*8

In [2]:
x_loaded = {}

In [7]:
for q in range(10, 41):

    # Replace 'path/to/your/folder' with the folder path you want to check
    folder_path = '/raid/pranjul/DG3_HG_heatmaps_c/S'+ str(q) +'_fix_c'
    
    if folder_exists(folder_path):
        # Open a file in binary write mode
        with open('/raid/pranjul/DG3_HG_heatmaps_c/S'+ str(q) +'_fix_c/' + 'S'+ str(q) + '.pkl', 'rb') as file:
            x_loaded[q] = pickle.load(file)

#x_loaded = [x.tolist() for x in x_loaded]

In [8]:
len(x_loaded)

37

In [ ]:
x_loaded

In [ ]:
x_loaded[4]

In [ ]:
plt.imshow(x_loaded[4][0][0])

In [ ]:
plt.imshow(x_loaded[4][0][4])

In [10]:
256*37

9472

In [ ]:
for i in range(2):
    print(f"Iter:{i+1}")


In [9]:
import pandas as pd

# Assuming x_loaded is a dictionary
data_frames = []

for key, value in x_loaded.items():
    df = pd.DataFrame(value, columns=['dg3', 'stim_folder', 'stim_name', 'sub', 'hg'])
    data_frames.append(df)

# Concatenate DataFrames
df = pd.concat(data_frames, ignore_index=True)

# Display the resulting DataFrame
print(df)


                                                    dg3     stim_folder  \
0     [[-21.89091177095421, -21.89091177095421, -21....      pareidolia   
1     [[-23.752590900618024, -23.752590900618024, -2...  pareidolia_inv   
2     [[-22.717763718089778, -22.717763718089778, -2...           faces   
3     [[-23.13883206422637, -23.13883206422637, -23....         objects   
4     [[-20.465820021512595, -20.465820021512595, -2...  pareidolia_inv   
...                                                 ...             ...   
9204  [[-22.03320704181483, -22.03320704181483, -22....     objects_inv   
9205  [[-19.347162311089896, -19.347162311089896, -1...  pareidolia_inv   
9206  [[-21.903870228837253, -21.903870228837253, -2...         objects   
9207  [[-19.344542363086855, -19.344542363086855, -1...       faces_inv   
9208  [[-24.540417387594943, -24.540417387594943, -2...  pareidolia_inv   

         stim_name  sub                                                 hg  
0               64  S0

In [11]:
df_agg_hg = df.groupby(['stim_folder', 'stim_name'])['hg'].apply(lambda x: np.mean(x.tolist(), axis=0)).reset_index()


In [12]:
df_agg_hg

stim_folder stim_name  \
0             faces    face01   
1             faces    face02   
2             faces    face03   
3             faces    face04   
4             faces    face05   
..              ...       ...   
251  pareidolia_inv    75_inv   
252  pareidolia_inv    78_inv   
253  pareidolia_inv    80_inv   
254  pareidolia_inv    81_inv   
255  pareidolia_inv    83_inv   

                                                    hg  
0    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
1    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
2    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
3    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
4    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
..                                                 ...  
251  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
252  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
253  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
254  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
255  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  

[256 rows x 3 columns]

In [14]:

import base64
# Define a function to serialize the 2D arrays
def serialize_array(arr):
    return base64.b64encode(pickle.dumps(arr)).decode('utf-8')

# Apply the serialization function to the column
df_agg_hg['hg'] = df_agg_hg['hg'].apply(serialize_array)

# Save the DataFrame to a CSV file
df_agg_hg.to_csv('/raid/pranjul/agg_hg_37_subs_c.csv', index=False)

In [15]:


# Load the DataFrame from the CSV file
loaded_df_csv = pd.read_csv('/raid/pranjul/agg_hg_37_subs_c.csv')

# Define a function to deserialize the 2D arrays
def deserialize_array(serialized_arr):
    return pickle.loads(base64.b64decode(serialized_arr.encode('utf-8')))

# Apply the deserialization function to the column
loaded_df_csv['hg'] = loaded_df_csv['hg'].apply(deserialize_array)

# Now, loaded_df contains the original DataFrame with 2D arrays in 'Array_Column'

In [16]:
loaded_df_csv

stim_folder stim_name  \
0             faces    face01   
1             faces    face02   
2             faces    face03   
3             faces    face04   
4             faces    face05   
..              ...       ...   
251  pareidolia_inv    75_inv   
252  pareidolia_inv    78_inv   
253  pareidolia_inv    80_inv   
254  pareidolia_inv    81_inv   
255  pareidolia_inv    83_inv   

                                                    hg  
0    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
1    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
2    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
3    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
4    [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
..                                                 ...  
251  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
252  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
253  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
254  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  
255  [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...  

[256 rows x 3 columns]

In [ ]:
sp_corr = []
for i in range(len(df['dg3'])):
    sp_corr.append(spearmanr(df['dg3'][i].flatten(), df['hg'][i].flatten())[0])
    #break


In [ ]:
import pickle

# Save the list to a file
with open('/raid/pranjul/sp_corr_dg3_37_subs_c.pkl', 'wb') as file:
    pickle.dump(sp_corr, file)

In [ ]:
# Load the list from the file
with open('/raid/pranjul/sp_corr_dg3_37_subs_c.pkl', 'rb') as file:
    loaded_list = pickle.load(file)

print(loaded_list)

In [ ]:
df

In [ ]:
# Add the Spearman correlation values to the DataFrame
df['sp_corr'] = sp_corr

In [ ]:
df = df.drop(columns=['dg3', 'hg'])

In [ ]:
len(df['sp_corr'])

In [ ]:
df

In [ ]:
result_df

In [ ]:
# Define the custom order
custom_order = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']

# Convert the 'stim_folder' column to a Categorical data type with the custom order
result_df['stim_folder'] = pd.Categorical(result_df['stim_folder'], categories=custom_order, ordered=True)

# Sort the DataFrame based on the custom order
df_sorted = result_df.sort_values(by='stim_folder')

# Print the sorted DataFrame
print(df_sorted)

In [ ]:
result_df

In [ ]:
df['stim_folder']

In [ ]:
df['stim_folder'].value_counts()

In [ ]:
result_df['stim_folder'].value_counts()

In [ ]:
import pandas as pd
import numpy as np

# Assuming df is your original DataFrame
# If you don't have a DataFrame, you can create a sample one
# df = pd.DataFrame({'stim_folder': ['objects']*32 + ['faces']*32 + ['pareidolia']*31 + ['pareidolia_art_inv']*31 + ['pareidolia_inv']*31 + ['pareidolia_art']*31 + ['objects_inv']*31 + ['faces_inv']*30})

# Get the unique values and their counts
value_counts = df['stim_folder'].value_counts()

# Find the minimum count
min_count = value_counts.min()

# Identify rows to be removed for each unique value
rows_to_remove = []

for stim_folder, count in value_counts.items():
    if count > min_count:
        indices = df[df['stim_folder'] == stim_folder].sample(n=count - min_count).index
        rows_to_remove.extend(indices)

# Remove the identified rows
result_df = df.drop(rows_to_remove)

# Display the result DataFrame
print(result_df)


In [ ]:
min_count

In [ ]:
len(rows_to_remove)

In [ ]:
from itertools import combinations

# 'Object_and_face_identification'
# Given array
task_array = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']

# Generate all unique combinations of two tasks
combinations_list = list(combinations(task_array, 2))

# Display the result
print(combinations_list)

In [ ]:
len(df['sp_corr'])

In [ ]:
df

In [ ]:
df["stim_folder"]

In [ ]:
df["sp_corr"]

In [ ]:
combinations_list

In [ ]:
result_df

In [ ]:
df_sorted

In [ ]:
result_df

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from statannotations.Annotator import Annotator

x = "stim_folder"
y = "sp_corr"

# Filter the DataFrame based on the 'Time' condition
subset_df = df_sorted

# Increase the figure size and font size
plt.figure(figsize=(6, 4))
sns.set(style="white", rc={"axes.edgecolor": "black", "grid.color": "black", "grid.linestyle": ":"}, font_scale=1.5)

# Create a palette with distinct colors
palette = sns.color_palette("Set3", n_colors=len(subset_df[x].unique()))  # You can choose any other colormap

# Create the barplot with the distinct color palette
ax = sns.barplot(data=subset_df, x=x, y=y, palette=palette, capsize=0.1, errwidth=1.5)  # Added capsize and errwidth for error bars
#ax = sns.boxplot(data=subset_df, x=x, y=y, palette=palette)  # Added capsize and errwidth for error bars

'''
# Add statistical annotations
annot = Annotator(ax, combinations_list, data=subset_df, x=x, y=y)
annot.new_plot(ax, combinations_list,
               data=subset_df, x=x, y=y)
annot.configure(test='Kruskal', text_format='star', loc='outside',
                comparisons_correction="fdr_bh",
                hide_non_significant=True,
                pvalue_thresholds=[[1e-3, '∗∗∗'], [1e-2, "∗∗"], [0.05, "∗"]], verbose=2)

#annot.apply_test()

# Adjust the position of stars between lines
#annot.line_offset_to_group = 0.5
#annot.line_offset = 0.3  # Adjust this value to move the stars closer to the lines
#annot.text_offset = 0.05  # Adjust this value to move the stars closer to the lines
#ax, test_results = annot.annotate(line_offset = 0.01)
#ax, test_results = annot.annotate()

ax, test_results = annot.apply_test().annotate(line_offset=0.001)
'''
# Remove top and right plot edges
sns.despine()

# Define explicit legend handles
legend_labels = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']
legend_handles = [plt.Rectangle((0, 0), 1, 1, color=color, label=label) for color, label in zip(palette, legend_labels)]

# Create legend without edges and without error bars, and change the title to "CNN"
legend = ax.legend(handles=legend_handles, title="", title_fontsize='16', loc='upper left', bbox_to_anchor=(1, 1), frameon=False, fontsize=16)



# Remove x-axis ticks and labels
#ax.set_xticks([])
#ax.set_xticklabels([])

# Set y-axis limits from 0 to 1
ax.set_ylim(0.25, 0.35)
ax.set_yticks(np.linspace(0.25, 0.35, num=6))

# Show the tick marks on the left side of the y-axis
#ax.tick_params(axis='y', direction='out', length=5)  # Adjust 'length' as needed
ax.tick_params(tick1On=True)

# Set font size for axis labels and title
ax.set_ylabel('DG3 & HG correlation [Spearman\'s r]', fontsize=16)
#ax.set_ylabel('')
ax.set_xlabel('2 (orientation)  x 4 (stimuli condition)', fontsize=16)

#ax.set_title('255ms:lay13-15', fontsize=18)

# Set font size for tick labels
ax.tick_params(axis='both', labelsize=16)

# Uncomment the following lines to show y-axis ticks and tick labels
# ax.set_yticks(np.linspace(0, 1.0, num=11))  # Uncomment if not already set
# ax.set_yticklabels(['0.0', '0.1', '0.2', '0.3', '0.4', '0.5', '0.6', '0.7', '0.8', '0.9', '1.0'])

#plt.savefig('fig_5_3.png', dpi= 600, bbox_inches='tight')
#plt.savefig('fig_5_3.png', dpi= 600)


# Show the plot
plt.show()


In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from statannotations.Annotator import Annotator

x = "stim_folder"
y = "sp_corr"

# Filter the DataFrame based on the 'Time' condition
subset_df = result_df

# Increase the figure size and font size
plt.figure(figsize=(6, 4))
sns.set(style="white", rc={"axes.edgecolor": "black", "grid.color": "black", "grid.linestyle": ":"}, font_scale=1.5)

# Create a palette with distinct colors
palette = sns.color_palette("Set3", n_colors=len(subset_df[x].unique()))  # You can choose any other colormap

# Create the barplot with the distinct color palette
ax = sns.barplot(data=subset_df, x=x, y=y, palette=palette, capsize=0.1, errwidth=1.5)  # Added capsize and errwidth for error bars
# ax = sns.boxplot(data=subset_df, x=x, y=y, palette=palette)  # Added capsize and errwidth for error bars


# Add statistical annotations
annot = Annotator(ax, combinations_list, data=subset_df, x=x, y=y)
annot.new_plot(ax, combinations_list,
               data=subset_df, x=x, y=y)
annot.configure(test='Kruskal', text_format='star', loc='outside',
                comparisons_correction="fdr_bh",
                hide_non_significant=True,
                pvalue_thresholds=[[1e-3, '∗∗∗'], [1e-2, "∗∗"], [0.05, "∗"]], verbose=2, line_height = .05)

#annot.apply_test()

# Adjust the position of stars between lines
#annot.line_offset_to_group = 0.5
#annot.line_offset = 0.3  # Adjust this value to move the stars closer to the lines
#annot.text_offset = 0.05  # Adjust this value to move the stars closer to the lines
#ax, test_results = annot.annotate(line_offset = 0.01)
#ax, test_results = annot.annotate()

ax, test_results = annot.apply_test().annotate(line_offset=0.001)

# Remove top and right plot edges
sns.despine()

# Define explicit legend handles
legend_labels = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']
legend_handles = [plt.Rectangle((0, 0), 1, 1, color=color, label=label) for color, label in zip(palette, legend_labels)]

# Create legend without edges and without error bars, and change the title to "CNN"
legend = ax.legend(handles=legend_handles, title="", title_fontsize='16', loc='upper left', bbox_to_anchor=(1, 1), frameon=False, fontsize=16)



# Remove x-axis ticks and labels
#ax.set_xticks([])
#ax.set_xticklabels([])

# Set y-axis limits from 0 to 1
#ax.set_ylim(0.25, 0.35)
#ax.set_yticks(np.linspace(0.25, 0.35, num=6))

# Show the tick marks on the left side of the y-axis
#ax.tick_params(axis='y', direction='out', length=5)  # Adjust 'length' as needed
ax.tick_params(tick1On=True)

# Set font size for axis labels and title
ax.set_ylabel('DG3 & HG correlation [Spearman\'s r]', fontsize=16)
#ax.set_ylabel('')
#ax.set_xlabel('2 (orientation)  x 4 (stimuli condition)', fontsize=16)
ax.set_xticklabels(ax.get_xticklabels(), rotation=90)


#ax.set_title('255ms:lay13-15', fontsize=18)

# Set font size for tick labels
ax.tick_params(axis='both', labelsize=16)

# Uncomment the following lines to show y-axis ticks and tick labels
# ax.set_yticks(np.linspace(0, 1.0, num=11))  # Uncomment if not already set
#ax.set_yticklabels(['0.0', '0.1', '0.2', '0.3', '0.4', '0.5', '0.6', '0.7', '0.8', '0.9', '1.0'])

#plt.savefig('fig_5_3.png', dpi= 600, bbox_inches='tight')
#plt.savefig('fig_5_3.png', dpi= 600)


# Show the plot
plt.show()


In [ ]:
print("Length of x:", len(subset_df[x]))
print("Length of y:", len(subset_df[y]))

In [ ]:
loaded_df_csv

In [ ]:
df_agg_hg = loaded_df_csv

In [ ]:
import numpy as np
from scipy.misc import face
from scipy.ndimage import zoom
from scipy.special import logsumexp
import torch
import matplotlib.pyplot as plt

import deepgaze_pytorch

DEVICE = 'cuda'

# you can use DeepGazeI or DeepGazeIIE
model = deepgaze_pytorch.DeepGazeIIE(pretrained=True).to(DEVICE)

# image = face()

x = []


for i in range(len(df_agg_hg)):
    
    stim_folder_name = df_agg_hg['stim_folder'][i]
    stim_image_name = df_agg_hg['stim_name'][i]
        
    folder_path = '/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/DG2E_HG_heatmaps_c/'
    
    image = cv2.imread('/home/pranjul/DeepGaze/Bachelorarbeit_Christine_Huschens/stimuli/' + stim_folder_name + '/' + stim_image_name + '.tif')
    #create_folder(os.path.join(folder_path, stim_folder_name))

    #image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    image = cv2.resize(image, (1200, 1200))  
    
    # load precomputed centerbias log density (from MIT1003) over a 1024x1024 image
    # you can download the centerbias from https://github.com/matthias-k/DeepGaze/releases/download/v1.0.0/centerbias_mit1003.npy
    # alternatively, you can use a uniform centerbias via `centerbias_template = np.zeros((1024, 1024))`.
    centerbias_template = np.load('centerbias_mit1003.npy')
    # centerbias_template = np.zeros((1024, 1024))
    # rescale to match image size
    centerbias = zoom(centerbias_template, (image.shape[0]/centerbias_template.shape[0], image.shape[1]/centerbias_template.shape[1]), order=0, mode='nearest')
    # renormalize log density
    centerbias -= logsumexp(centerbias)

    image_tensor = torch.tensor([image.transpose(2, 0, 1)]).to(DEVICE)
    centerbias_tensor = torch.tensor([centerbias]).to(DEVICE)

    log_density_prediction = model(image_tensor, centerbias_tensor)
    
    a = log_density_prediction.detach().cpu().numpy()[0,0]
    
    x.append(a)
    
    '''
    f, axs = plt.subplots(nrows=1, ncols=2, figsize=(16, 9))
    axs[0].imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    # axs[0].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
    # axs[0].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='yellow', zorder=100)
    axs[0].set_axis_off()
    axs[1].matshow(log_density_prediction.detach().cpu().numpy()[0, 0])  # first image in batch, first (and only) channel
    # axs[1].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
    # axs[1].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='yellow', zorder=100)
    axs[1].set_axis_off()
    # plt.savefig(os.path.join('DG2_heatmaps', '{0}.jpg'.format(i)))
    
    
    f, axs = plt.subplots(nrows=1, ncols=3, figsize=(16, 9))
    axs[0].imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    #axs[0].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
    #axs[0].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
    axs[0].set_axis_off()
    axs[1].matshow(log_density_prediction.detach().cpu().numpy()[0, 0])  # first image in batch, first (and only) channel
    #axs[1].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
    #axs[1].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
    axs[1].set_axis_off()
    axs[2].matshow(df_agg_hg['hg'][i])
    #axs[2].plot(fixation_history_x, fixation_history_y, 'o-', color='red')
    #axs[2].scatter(fixation_history_x[-1], fixation_history_y[-1], 100, color='white', zorder=100)
    axs[2].set_axis_off()
    plt.tight_layout()
    plt.savefig(os.path.join(folder_path, stim_folder_name, stim_image_name + '.png'))
    #plt.show()
    plt.close()
    '''
    
    #break

In [ ]:
len(x)

In [ ]:
# Add the Spearman correlation values to the DataFrame
df_agg_hg['dg2'] = x

In [ ]:
df_agg_hg

In [ ]:


# Define a function to serialize the 2D arrays
def serialize_array(arr):
    return base64.b64encode(pickle.dumps(arr)).decode('utf-8')

# Apply the serialization function to the column
df_agg_hg['hg'] = df_agg_hg['hg'].apply(serialize_array)

# Apply the serialization function to the column
df_agg_hg['dg2'] = df_agg_hg['dg2'].apply(serialize_array)

# Save the DataFrame to a CSV file
df_agg_hg.to_csv('/raid/pranjul/agg_hg_dg2_26_subs_c.csv', index=False)

In [ ]:
import base64

# Load the DataFrame from the CSV file
loaded_df_csv = pd.read_csv('/raid/pranjul/agg_hg_dg2_26_subs_c.csv')

# Define a function to deserialize the 2D arrays
def deserialize_array(serialized_arr):
    return pickle.loads(base64.b64decode(serialized_arr.encode('utf-8')))

# Apply the deserialization function to the column
loaded_df_csv['hg'] = loaded_df_csv['hg'].apply(deserialize_array)

# Apply the deserialization function to the column
loaded_df_csv['dg2'] = loaded_df_csv['dg2'].apply(deserialize_array)

# Now, loaded_df contains the original DataFrame with 2D arrays in 'Array_Column'

In [ ]:
loaded_df_csv

In [ ]:
import pandas as pd

# Create two sample dataframes
data1 = {'SharedColumn': [1, 2, 3, 4, 5],
         'Data1_Column': ['A', 'B', 'C', 'D', 'E']}
df1 = pd.DataFrame(data1)

data2 = {'SharedColumn': [1, 1, 2, 2, 3],
         'Data2_Column': [10, 20, 30, 40, 50]}
df2 = pd.DataFrame(data2)

# Merge dataframes based on the shared column
merged_df = pd.merge(df1, df2, on='SharedColumn', how='outer')

# Divide the dataframes based on unique values in the 'SharedColumn'
unique_values_df1 = merged_df[merged_df['Data2_Column'].isnull()].drop('Data2_Column', axis=1)
repeated_values_df2 = merged_df[merged_df['Data1_Column'].notnull()].drop('Data1_Column', axis=1)

# Display the results
print("Unique Values in df1:")
print(unique_values_df1)

print("\nRepeated Values in df2:")
print(repeated_values_df2)


In [ ]:
df1

In [ ]:
df2

In [ ]:
pd.merge(loaded_df_csv, df_sh, on='stim_folder', how='outer')

In [ ]:
sp_corr_dg2 = []
for i in range(len(loaded_df_csv)):
    sp_corr_dg2.append(spearmanr(loaded_df_csv['dg2'][i].flatten(), loaded_df_csv['hg'][i].flatten())[0])
    #break

In [ ]:
# Add the Spearman correlation values to the DataFrame
loaded_df_csv['sp_corr_dg2'] = sp_corr_dg2

In [ ]:
loaded_df_csv

In [ ]:
loaded_df_csv = loaded_df_csv.drop(columns=['dg2', 'hg'])

In [ ]:
loaded_df_csv

In [ ]:
loaded_df_csv['stim_folder'].value_counts()

In [ ]:
# Define the custom order
custom_order = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']

# Convert the 'stim_folder' column to a Categorical data type with the custom order
loaded_df_csv['stim_folder'] = pd.Categorical(loaded_df_csv['stim_folder'], categories=custom_order, ordered=True)

# Sort the DataFrame based on the custom order
df_sorted = loaded_df_csv.sort_values(by='stim_folder')

# Print the sorted DataFrame
print(df_sorted)

In [ ]:
df_sorted

In [ ]:
df_sorted_sh = pd.merge(df_sorted, df_sh, on='stim_folder', how='outer')

In [ ]:
df_sorted_sh

In [ ]:
# Divide Column1 by Column2
df_sorted_sh['sh_corrected'] = df_sorted_sh['sp_corr_dg2'] / df_sorted_sh['sp_corr_splt_hlf']

In [ ]:
df_sorted_sh

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from statannotations.Annotator import Annotator

x = "stim_folder"
y = "sh_corrected"

# Filter the DataFrame based on the 'Time' condition
subset_df = df_sorted_sh

# Increase the figure size and font size
plt.figure(figsize=(6, 4))
sns.set(style="white", rc={"axes.edgecolor": "black", "grid.color": "black", "grid.linestyle": ":"}, font_scale=1.5)

# Create a palette with distinct colors
palette = sns.color_palette("Set3", n_colors=len(subset_df[x].unique()))  # You can choose any other colormap

# Create the barplot with the distinct color palette
ax = sns.barplot(data=subset_df, x=x, y=y, palette=palette, capsize=0.1, errwidth=1.5)  # Added capsize and errwidth for error bars
# ax = sns.boxplot(data=subset_df, x=x, y=y, palette=palette)  # Added capsize and errwidth for error bars


# Add statistical annotations
annot = Annotator(ax, combinations_list, data=subset_df, x=x, y=y)
annot.new_plot(ax, combinations_list,
               data=subset_df, x=x, y=y)
annot.configure(test='Kruskal', text_format='star', loc='outside',
                comparisons_correction="fdr_bh",
                hide_non_significant=True,
                pvalue_thresholds=[[1e-3, '∗∗∗'], [1e-2, "∗∗"], [0.05, "∗"]], verbose=2, line_height = .05)

#annot.apply_test()

# Adjust the position of stars between lines
#annot.line_offset_to_group = 0.5
#annot.line_offset = 0.3  # Adjust this value to move the stars closer to the lines
#annot.text_offset = 0.05  # Adjust this value to move the stars closer to the lines
#ax, test_results = annot.annotate(line_offset = 0.01)
#ax, test_results = annot.annotate()

ax, test_results = annot.apply_test().annotate(line_offset=0.2)

# Remove top and right plot edges
sns.despine()

# Define explicit legend handles
legend_labels = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']
legend_handles = [plt.Rectangle((0, 0), 1, 1, color=color, label=label) for color, label in zip(palette, legend_labels)]

# Create legend without edges and without error bars, and change the title to "CNN"
legend = ax.legend(handles=legend_handles, title="", title_fontsize='16', loc='upper left', bbox_to_anchor=(1, 1), frameon=False, fontsize=16)



# Remove x-axis ticks and labels
#ax.set_xticks([])
#ax.set_xticklabels([])

# Set y-axis limits from 0 to 1
ax.set_ylim(0.9, 1.1)
ax.set_yticks(np.linspace(0.9, 1.1, num=11))

# Show the tick marks on the left side of the y-axis
#ax.tick_params(axis='y', direction='out', length=5)  # Adjust 'length' as needed
ax.tick_params(tick1On=True)

# Set font size for axis labels and title
ax.set_ylabel('S-H corrected DG2E & HG correlation \n [Spearman\'s r]', fontsize=16)
#ax.set_ylabel('')
#ax.set_xlabel('2 (orientation)  x 4 (stimuli condition)', fontsize=16)
ax.set_xticklabels(ax.get_xticklabels(), rotation=90)


#ax.set_title('255ms:lay13-15', fontsize=18)

# Set font size for tick labels
ax.tick_params(axis='both', labelsize=16)

# Uncomment the following lines to show y-axis ticks and tick labels
# ax.set_yticks(np.linspace(0, 1.0, num=11))  # Uncomment if not already set
#ax.set_yticklabels(['0.0', '0.1', '0.2', '0.3', '0.4', '0.5', '0.6', '0.7', '0.8', '0.9', '1.0'])

#plt.savefig('fig_5_3.png', dpi= 600, bbox_inches='tight')
#plt.savefig('fig_5_3.png', dpi= 600)


# Show the plot
plt.show()


In [ ]:
# Get all unique values in the 'sub' column
unique_subs = df['sub'].unique()
unique_subs

In [ ]:
# Randomly shuffle the unique values
np.random.shuffle(unique_subs)
unique_subs

In [ ]:
# Calculate the index to split at (half of the unique values)
split_index = len(unique_subs) // 2
split_index

In [ ]:
# Select the first half of unique values
selected_subs_df1 = unique_subs[:split_index]
selected_subs_df1

In [ ]:
# Split the DataFrame into two based on the selected unique values
df1 = df[df['sub'].isin(selected_subs_df1)]
df2 = df[~df['sub'].isin(selected_subs_df1)]

In [ ]:
df1

In [ ]:
df2

In [ ]:
df1_hg = df1.groupby(['stim_folder', 'stim_name'])['hg'].apply(lambda x: np.mean(x.tolist(), axis=0)).reset_index()

# Rename the column 'old_col_name' to 'new_col_name'
df1_hg = df1_hg.rename(columns={'hg': 'hg_1'})
df1_hg

In [ ]:
df2_hg = df2.groupby(['stim_folder', 'stim_name'])['hg'].apply(lambda x: np.mean(x.tolist(), axis=0)).reset_index()

# Rename the column 'old_col_name' to 'new_col_name'
df2_hg = df2_hg.rename(columns={'hg': 'hg_2'})
df2_hg

In [ ]:
# Merge the DataFrames based on 'stim_folder' and 'stim_name'
merged_df = pd.merge(df1_hg, df2_hg, on=['stim_folder', 'stim_name'], how='inner')

# Display the resulting merged DataFrame
print(merged_df)

In [ ]:
plt.imshow(merged_df['hg_1'][1])

In [ ]:
plt.imshow(merged_df['hg_2'][1])

In [ ]:
sp_corr_splt_hlf = []
for i in range(len(merged_df)):
    sp_corr_splt_hlf.append(spearmanr(merged_df['hg_1'][i].flatten(), merged_df['hg_2'][i].flatten())[0])
    #break

In [ ]:
# Add the Spearman correlation values to the DataFrame
merged_df['sp_corr_splt_hlf'] = sp_corr_splt_hlf

In [ ]:
merged_df = merged_df.drop(columns=['hg_1', 'hg_2'])

In [ ]:
merged_df

In [ ]:
merged_df = merged_df.groupby('stim_folder')['sp_corr_splt_hlf'].mean().reset_index()
merged_df

In [ ]:
# Define the custom order
custom_order = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']

# Convert the 'stim_folder' column to a Categorical data type with the custom order
merged_df['stim_folder'] = pd.Categorical(merged_df['stim_folder'], categories=custom_order, ordered=True)

# Sort the DataFrame based on the custom order
merged_df_sorted = merged_df.sort_values(by='stim_folder')

# Print the sorted DataFrame
print(merged_df_sorted)

In [ ]:
# Extract the 'sp_corr_splt_hlf' column and save it to a NumPy array
sp_corr_splt_hlf_array = merged_df_sorted['sp_corr_splt_hlf'].to_numpy()

In [ ]:
sp_corr_splt_hlf_array

In [ ]:
# Number of times to perform the bootstrap sampling
num_iterations = 50
sp_corr_splt_hlf_array = []

for _ in range(num_iterations):

    # Get all unique values in the 'sub' column
    unique_subs = df['sub'].unique()
    #print(unique_subs)

    # Randomly shuffle the unique values
    np.random.shuffle(unique_subs)
    print(unique_subs)

    # Calculate the index to split at (half of the unique values)
    split_index = len(unique_subs) // 2
    #print(split_index)

    # Select the first half of unique values
    selected_subs_df1 = unique_subs[:split_index]
    #selected_subs_df1

    # Split the DataFrame into two based on the selected unique values
    df1 = df[df['sub'].isin(selected_subs_df1)]
    df2 = df[~df['sub'].isin(selected_subs_df1)]

    df1_hg = df1.groupby(['stim_folder', 'stim_name'])['hg'].apply(lambda x: np.mean(x.tolist(), axis=0)).reset_index()

    # Rename the column 'old_col_name' to 'new_col_name'
    df1_hg = df1_hg.rename(columns={'hg': 'hg_1'})
    #df1_hg

    df2_hg = df2.groupby(['stim_folder', 'stim_name'])['hg'].apply(lambda x: np.mean(x.tolist(), axis=0)).reset_index()

    # Rename the column 'old_col_name' to 'new_col_name'
    df2_hg = df2_hg.rename(columns={'hg': 'hg_2'})
    #df2_hg

    # Merge the DataFrames based on 'stim_folder' and 'stim_name'
    merged_df = pd.merge(df1_hg, df2_hg, on=['stim_folder', 'stim_name'], how='inner')

    # Display the resulting merged DataFrame
    #print(merged_df)

    sp_corr_splt_hlf = []
    for i in range(len(merged_df)):
        sp_corr_splt_hlf.append(spearmanr(merged_df['hg_1'][i].flatten(), merged_df['hg_2'][i].flatten())[0])
        #break

    # Add the Spearman correlation values to the DataFrame
    merged_df['sp_corr_splt_hlf'] = sp_corr_splt_hlf

    merged_df = merged_df.drop(columns=['hg_1', 'hg_2'])

    merged_df = merged_df.groupby('stim_folder')['sp_corr_splt_hlf'].mean().reset_index()

    # Define the custom order
    custom_order = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']

    # Convert the 'stim_folder' column to a Categorical data type with the custom order
    merged_df['stim_folder'] = pd.Categorical(merged_df['stim_folder'], categories=custom_order, ordered=True)

    # Sort the DataFrame based on the custom order
    merged_df_sorted = merged_df.sort_values(by='stim_folder')

    # Print the sorted DataFrame
    #print(merged_df_sorted)

    # Extract the 'sp_corr_splt_hlf' column and save it to a NumPy array
    sp_corr_splt_hlf_array.append(merged_df_sorted['sp_corr_splt_hlf'].to_numpy())

print(sp_corr_splt_hlf_array)


In [ ]:
np.mean(sp_corr_splt_hlf_array, axis=0)

In [ ]:
len(sp_corr_splt_hlf_array)

In [ ]:
from tabulate import tabulate

mapping = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']
values = [0.64045339, 0.63962363, 0.65247639, 0.64685355, 0.69212828, 0.68226111, 0.63446804, 0.64820666]

array_result = np.array(values)

table = list(zip(mapping, array_result))
headers = ["Conditions", "S-H rho"]

print(tabulate(table, headers=headers))

In [ ]:
# Given data
mapping = ['faces', 'faces_inv', 'objects', 'objects_inv', 'pareidolia', 'pareidolia_inv', 'pareidolia_art', 'pareidolia_art_inv']
values = [0.64045339, 0.63962363, 0.65247639, 0.64685355, 0.69212828, 0.68226111, 0.63446804, 0.64820666]

# Create a DataFrame
df_sh = pd.DataFrame({'stim_folder': mapping, 'sp_corr_splt_hlf': values})

# Print the DataFrame
print(df_sh)

In [ ]:

correlation_coef_objects_iter_img = []

for keys in y_objects:
    mmm = []
    print(keys)
    for i in range(len(y_objects_subs)):
        if y_objects_subs[i][0][0] == keys:
            mmm.append(y_objects_subs[i][1])
            #print(y_faces_subs[i][1])

    # Number of times to perform the bootstrap sampling
    num_iterations = 50
    correlation_coef_objects_iter = []

    for _ in range(num_iterations):

        # Define your dataset
        dataset = list(range(len(mmm)))

        # Perform bootstrap sampling without replacement until no dataset is left
        bootstrap_samples = []
        correlation_coef_objects = []

        while dataset:
            bootstrap_sample = random.sample(dataset, len(dataset))
            bootstrap_samples.append(bootstrap_sample)
            dataset = [x for x in dataset if x not in bootstrap_sample]

        # Print the bootstrap samples
        #for i, sample in enumerate(bootstrap_samples):
        #    print(f"Bootstrap Sample {k + 1}: {sample}")
        
        temp1 = []
        temp2 = []

        for i in bootstrap_samples[0][:int(len(bootstrap_samples[0])/2)]:
            temp1.append(mmm[i])

        for i in bootstrap_samples[0][int(len(bootstrap_samples[0])/2):]:
            temp2.append(mmm[i])

        #print(temp1)
        temp1 = np.mean(temp1, axis=0)
        temp2 = np.mean(temp2, axis=0)
            
            #plt.matshow(mmm[sample[i]])
            #plt.matshow(mmm[sample[i+1]])
        correlation_coef_objects.append(spearmanr(temp1.flatten(),
                                                temp2.flatten())[0])

        correlation_coef_objects_iter.append(np.mean(correlation_coef_objects))
        
        #break
        

    correlation_coef_objects_iter_img.append(np.mean(correlation_coef_objects_iter))
        
    #break
    